# 광진구 공원 입지 feature importance 도출 분석

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# 작업 디렉토리 설정
import os
wd = '/content/drive/MyDrive/광진구 공모전 DB/광진구 공모전 데이터/db/전처리 끝난 데이터'
os.chdir(wd)
os.getcwd()

'/content/drive/.shortcut-targets-by-id/1x0l2MxUZZl6XKOnBiXhTarE4yqgw4tkg/광진구 공모전 데이터/db/전처리 끝난 데이터'

In [ ]:
import pandas as pd
import geopandas as gpd

In [ ]:
!sudo apt-get install -y fonts-nanum
!sudo fc-cache -fv
!rm ~/.cache/matplotlib -rf

import matplotlib.pyplot as plt
import matplotlib.font_manager as fm
fm.fontManager.addfont('/usr/share/fonts/truetype/nanum/NanumBarunGothic.ttf')
plt.rc('font', family='NanumBarunGothic')

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following NEW packages will be installed:
  fonts-nanum
0 upgraded, 1 newly installed, 0 to remove and 34 not upgraded.
Need to get 10.3 MB of archives.
After this operation, 34.1 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 fonts-nanum all 20200506-1 [10.3 MB]
Fetched 10.3 MB in 1s (10.4 MB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEnd/Dialog.pm line 78, <> line 1.)
debconf: falling back to frontend: Readline
debconf: unable to initialize frontend: Readline
debconf: (This frontend requires a controlling tty.)
debconf: falling back to frontend: Teletype
dpkg-preconfigure: unable to re-open stdin: 
Selecting previously unselected package fonts-nanum.
(Reading database ... 126101 files and direc

In [ ]:
path = "/content/drive/MyDrive/광진구 공모전 DB/광진구 공모전 데이터/db/1광진구_유소년_인구수_100/nlsp_021001004.shp"
gdf_child_parks = gpd.read_file(path, encoding='UTF-8')  # EPSG:5179
gdf_child_parks.loc[gdf_child_parks['val'] >= 240, 'val'] = 230
gdf_child_parks.head(3)

gid    lbl   val                                           geometry
0  다사633494  15.00  15.0  POLYGON ((963300 1949400, 963300 1949500, 9634...
1  다사626517  18.00  18.0  POLYGON ((962600 1951700, 962600 1951800, 9627...
2  다사642512  30.00  30.0  POLYGON ((964200 1951200, 964200 1951300, 9643...

## 0.광진구 내 공원(어린이공원/그 외)

### (1) 격자 데이터 좌표계 변환

In [ ]:
# 분석을 위해 투영 좌표계(EPSG:5181)로 변환(미터 단위)
grid_gdf_child_parks = gdf_child_parks.to_crs(epsg=5181)
grid_gdf_child_parks.head()

gid    lbl   val                                           geometry
0  다사633494  15.00  15.0  POLYGON ((207472.637 449302.001, 207472.105 44...
1  다사626517  18.00  18.0  POLYGON ((206760.14 451599.127, 206759.608 451...
2  다사642512  30.00  30.0  POLYGON ((208363.394 451107.457, 208362.861 45...
3  다사647489  71.00  71.0  POLYGON ((208875.816 448809.263, 208875.284 44...
4  다사640506  23.00  23.0  POLYGON ((208166.512 450506.17, 208165.98 4506...

## 1.초등학교

In [ ]:
df_elementary_schools = pd.read_csv('8초등학교.csv')
df_elementary_schools.head(2)

Unnamed: 0     학교명               도로명주소         위도          경도
0           0  세종초등학교   서울특별시 광진구 군자로 114  37.553011  127.072865
1           1  성동초등학교  서울특별시 광진구 자양로4길 63  37.533281  127.089281

In [ ]:
from shapely.geometry import Point

geometry = [Point(xy) for xy in zip(df_elementary_schools['경도'], df_elementary_schools['위도'])]
gdf_elementary_schools = gpd.GeoDataFrame(df_elementary_schools, geometry=geometry, crs='EPSG:4326')

gdf_elementary_schools = gdf_elementary_schools.to_crs(epsg=5181)
gdf_elementary_schools.head(2)

Unnamed: 0     학교명               도로명주소         위도          경도  \
0           0  세종초등학교   서울특별시 광진구 군자로 114  37.553011  127.072865   
1           1  성동초등학교  서울특별시 광진구 자양로4길 63  37.533281  127.089281   

                      geometry  
0  POINT (206438.53 450390.19)  
1  POINT (207891.21 448201.68)

In [ ]:
# 1. 격자 중심 계산
grid_gdf_child_parks['centroid'] = grid_gdf_child_parks.geometry.centroid

# 2. 좌표계 통일
gdf_elementary_schools = gdf_elementary_schools.to_crs(grid_gdf_child_parks.crs)

# 3. 초등학교 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_elementary_schools, grid_gdf_child_parks, how='left', predicate='within')

# 4. 각 격자 ID별 초등학교 수 계산
school_counts = gdf_joined.groupby('index_right').size()

# 5. 격자에 매핑
grid_gdf_child_parks['초등학교_수'] = grid_gdf_child_parks.index.map(school_counts).fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['초등학교_수'] != 0]

gid    lbl   val  \
37    다사631518  17.00  17.0   
87    다사629486  21.00  21.0   
153   다사648499  10.00  10.0   
400   다사631481  18.00  18.0   
471   다사629519  23.00  23.0   
481   다사622501   7.00   7.0   
515   다사620484    N/A   0.0   
592   다사639498    N/A   0.0   
679   다사625479  13.00  13.0   
943   다사639487   None   NaN   
993   다사629493   None   NaN   
995   다사645495   None   NaN   
1046  다사635501   None   NaN   
1065  다사637480   None   NaN   
1129  다사645505   None   NaN   
1267  다사622504   None   NaN   
1374  다사647491   None   NaN   
1629  다사637482   None   NaN   
1634  다사632510   None   NaN   
1802  다사622485   None   NaN   
1805  다사636520   None   NaN   

                                               geometry  \
37    POLYGON ((207259.793 451701.825, 207259.261 45...   
87    POLYGON ((207076.745 448499.578, 207076.213 44...   
153   POLYGON ((208970.534 449810.167, 208970.002 44...   
400   POLYGON ((207279.478 448000.457, 207278.946 44...   
471   POLYGON ((207059.187 451800.798, 207058.654 45...   
481   POLYGON ((206368.507 449996.408, 206367.975 45...   
515   POLYGON ((206177.476 448294.717, 206176.945 44...   
592   POLYGON ((208070.732 449705.342, 208070.2 4498...   
679   POLYGON ((206680.32 447797.192, 206679.788 447...   
943   POLYGON ((208076.583 448604.934, 208076.051 44...   
993   POLYGON ((207073.021 449199.837, 207072.489 44...   
995   POLYGON ((208672.55 449408.422, 208672.018 449...   
1046  POLYGON ((207668.987 450003.325, 207668.455 45...   
1065  POLYGON ((207880.232 447903.611, 207879.7 4480...   
1129  POLYGON ((208667.23 450408.794, 208666.698 450...   
1267  POLYGON ((206366.911 450296.519, 206366.379 45...   
1374  POLYGON ((208874.753 449009.338, 208874.221 44...   
1629  POLYGON ((207879.168 448103.685, 207878.637 44...   
1634  POLYGON ((207364.087 450902.061, 207363.555 45...   
1802  POLYGON ((206377.018 448395.818, 206376.486 44...   
1805  POLYGON ((207758.914 451904.56, 207758.381 452...   

                           centroid  초등학교_수  
37     POINT (207309.545 451752.11)     1.0  
87    POINT (207126.497 448549.862)     1.0  
153   POINT (209020.286 449860.452)     1.0  
400   POINT (207329.231 448050.741)     1.0  
471   POINT (207108.939 451851.082)     1.0  
481   POINT (206418.259 450046.692)     1.0  
515   POINT (206227.229 448345.001)     1.0  
592   POINT (208120.484 449755.626)     1.0  
679   POINT (206730.073 447847.476)     1.0  
943   POINT (208126.336 448655.218)     1.0  
993   POINT (207122.774 449250.121)     1.0  
995   POINT (208722.303 449458.707)     1.0  
1046   POINT (207718.74 450053.609)     1.0  
1065  POINT (207929.985 447953.895)     1.0  
1129  POINT (208716.982 450459.078)     1.0  
1267  POINT (206416.663 450346.803)     1.0  
1374  POINT (208924.505 449059.622)     1.0  
1629  POINT (207928.921 448153.969)     1.0  
1634   POINT (207413.84 450952.346)     1.0  
1802  POINT (206426.771 448446.102)     1.0  
1805  POINT (207808.666 451954.845)     1.0

## 2.유치원

In [ ]:
df_kindergartens= pd.read_csv('7유치원.csv')
df_kindergartens.head(2)

Unnamed: 0                                 유치원코드   유치원명  \
0          61  1ecec08c-eee1-b044-e053-0a32095ab044  선경유치원   
1          62  1ecec08c-eee2-b044-e053-0a32095ab044  성산유치원   

                    주소         위도          경도  
0  서울특별시 광진구 뚝섬로66길 14  37.533396  127.089785  
1  서울특별시 광진구 뚝섬로59길 18  37.532909  127.084178

In [ ]:
geometry = [Point(xy) for xy in zip(df_kindergartens['경도'], df_kindergartens['위도'])]
gdf_kindergartens = gpd.GeoDataFrame(df_kindergartens, geometry=geometry, crs='EPSG:4326')

gdf_kindergartens = gdf_kindergartens.to_crs(epsg=5181)
gdf_kindergartens.head(2)

Unnamed: 0                                 유치원코드   유치원명  \
0          61  1ecec08c-eee1-b044-e053-0a32095ab044  선경유치원   
1          62  1ecec08c-eee2-b044-e053-0a32095ab044  성산유치원   

                    주소         위도          경도                     geometry  
0  서울특별시 광진구 뚝섬로66길 14  37.533396  127.089785  POINT (207935.75 448214.45)  
1  서울특별시 광진구 뚝섬로59길 18  37.532909  127.084178  POINT (207440.17 448159.91)

In [ ]:
# 좌표계 통일
gdf_kindergartens = gdf_kindergartens.to_crs(grid_gdf_child_parks.crs)

# 유치원 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_kindergartens, grid_gdf_child_parks, how='left', predicate='within')

# 각 격자 ID별 유치원 수 계산
kindergartens_counts = gdf_joined.groupby('index_right').size()

# 격자에 매핑
grid_gdf_child_parks['유치원_수'] = grid_gdf_child_parks.index.map(kindergartens_counts).fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['유치원_수'] != 0]

gid     lbl    val  \
0     다사633494   15.00   15.0   
27    다사625484   27.00   27.0   
37    다사631518   17.00   17.0   
69    다사627519   14.00   14.0   
87    다사629486   21.00   21.0   
103   다사627489     N/A    0.0   
105   다사636495     N/A    0.0   
122   다사651499   33.00   33.0   
148   다사634523   31.00   31.0   
159   다사642493   60.00   60.0   
196   다사618483   32.00   32.0   
234   다사644505   19.00   19.0   
262   다사622508   19.00   19.0   
288   다사639493   55.00   55.0   
300   다사637483    9.00    9.0   
317   다사650494  136.00  136.0   
403   다사647492   30.00   30.0   
420   다사632482   13.00   13.0   
428   다사621506   15.00   15.0   
471   다사629519   23.00   23.0   
505   다사622503   38.00   38.0   
510   다사621485   85.00   85.0   
515   다사620484     N/A    0.0   
538   다사645489   53.00   53.0   
627   다사613486     N/A    0.0   
632   다사615493     N/A    0.0   
679   다사625479   13.00   13.0   
680   다사643506   39.00   39.0   
698   다사632480   42.00   42.0   
755   다사640503   28.00   28.0   
779   다사631510   35.00   35.0   
796   다사615487    6.00    6.0   
993   다사629493    None    NaN   
995   다사645495    None    NaN   
1046  다사635501    None    NaN   
1065  다사637480    None    NaN   
1751  다사627498    None    NaN   
1805  다사636520    None    NaN   

                                               geometry  \
0     POLYGON ((207472.637 449302.001, 207472.105 44...   
27    POLYGON ((206677.661 448297.376, 206677.129 44...   
37    POLYGON ((207259.793 451701.825, 207259.261 45...   
69    POLYGON ((206859.113 451799.733, 206858.581 45...   
87    POLYGON ((207076.745 448499.578, 207076.213 44...   
103   POLYGON ((206875.075 448798.625, 206874.543 44...   
105   POLYGON ((207772.217 449403.634, 207771.685 44...   
122   POLYGON ((209270.645 449811.763, 209270.113 44...   
148   POLYGON ((207557.243 452203.607, 207556.71 452...   
159   POLYGON ((208373.503 449206.752, 208372.971 44...   
196   POLYGON ((205977.935 448193.617, 205977.403 44...   
234   POLYGON ((208567.193 450408.262, 208566.661 45...   
262   POLYGON ((206364.782 450696.666, 206364.25 450...   
288   POLYGON ((208073.392 449205.156, 208072.86 449...   
300   POLYGON ((207878.637 448203.722, 207878.105 44...   
317   POLYGON ((209173.268 449311.045, 209172.736 44...   
403   POLYGON ((208874.221 449109.375, 208873.689 44...   
420   POLYGON ((207378.983 448101.025, 207378.451 44...   
428   POLYGON ((206265.81 450496.06, 206265.278 4505...   
471   POLYGON ((207059.187 451800.798, 207058.654 45...   
505   POLYGON ((206367.443 450196.482, 206366.911 45...   
510   POLYGON ((206276.981 448395.286, 206276.45 448...   
515   POLYGON ((206177.476 448294.717, 206176.945 44...   
538   POLYGON ((208675.742 448808.199, 208675.21 448...   
627   POLYGON ((205476.155 448491.068, 205475.623 44...   
632   POLYGON ((205672.505 449192.389, 205671.973 44...   
679   POLYGON ((206680.32 447797.192, 206679.788 447...   
680   POLYGON ((208466.624 450507.767, 208466.091 45...   
698   POLYGON ((207380.047 447900.951, 207379.515 44...   
755   POLYGON ((208168.109 450206.059, 208167.576 45...   
779   POLYGON ((207264.05 450901.529, 207263.518 451...   
796   POLYGON ((205675.697 448592.168, 205675.165 44...   
993   POLYGON ((207073.021 449199.837, 207072.489 44...   
995   POLYGON ((208672.55 449408.422, 208672.018 449...   
1046  POLYGON ((207668.987 450003.325, 207668.455 45...   
1065  POLYGON ((207880.232 447903.611, 207879.7 4480...   
1751  POLYGON ((206870.288 449698.957, 206869.756 44...   
1805  POLYGON ((207758.914 451904.56, 207758.381 452...   

                           centroid  초등학교_수  유치원_수  
0      POINT (207522.39 449352.286)     0.0    1.0  
27    POINT (206727.413 448347.661)     0.0    1.0  
37     POINT (207309.545 451752.11)     1.0    1.0  
69    POINT (206908.865 451850.018)     0.0    1.0  
87    POINT (207126.497 448549.862)     1.0    1.0  
103   POINT (206924.828 448848.909)     0.0    1.0  
105   POINT (207821.969 449453.919)     0.0    1.0

## 3.지역아동센터



In [ ]:
df_child_centers= pd.read_csv('6아동센터.csv')
df_child_centers.head(2)

Unnamed: 0        시설명                                시설주소      시설종류명(시설유형)  \
0          18  새움터지역아동센터  서울특별시 광진구 자양로 71-7, 3층 (자양동, 희년의집)  (아동복지시설) 지역아동센터   
1          19  해피엘지역아동센터            서울특별시 광진구 자양번영로 16 (자양동)  (아동복지시설) 지역아동센터   

          위도          경도  
0  37.534086  127.083905  
1  37.531005  127.075249

In [ ]:
geometry = [Point(xy) for xy in zip(df_child_centers['경도'], df_child_centers['위도'])]
gdf_child_centers = gpd.GeoDataFrame(df_child_centers, geometry=geometry, crs='EPSG:4326')

gdf_child_centers = gdf_child_centers.to_crs(epsg=5181)
gdf_child_centers.head(2)

Unnamed: 0        시설명                                시설주소      시설종류명(시설유형)  \
0          18  새움터지역아동센터  서울특별시 광진구 자양로 71-7, 3층 (자양동, 희년의집)  (아동복지시설) 지역아동센터   
1          19  해피엘지역아동센터            서울특별시 광진구 자양번영로 16 (자양동)  (아동복지시설) 지역아동센터   

          위도          경도                     geometry  
0  37.534086  127.083905  POINT (207415.95 448290.59)  
1  37.531005  127.075249  POINT (206651.19 447947.96)

In [ ]:
# 좌표계 통일
gdf_child_centers = gdf_child_centers.to_crs(grid_gdf_child_parks.crs)

# 아동센터 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_child_centers, grid_gdf_child_parks, how='left', predicate='within')

# 각 격자 ID별 아동센터 수 계산
child_centers_counts = gdf_joined.groupby('index_right').size()

# 격자에 매핑
grid_gdf_child_parks['지역아동센터_수'] = grid_gdf_child_parks.index.map(child_centers_counts).fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['지역아동센터_수'] != 0]

gid    lbl   val  \
107   다사640499  23.00  23.0   
214   다사624482    N/A   0.0   
252   다사612486   8.00   8.0   
262   다사622508  19.00  19.0   
335   다사632483   9.00   9.0   
344   다사636510    N/A   0.0   
396   다사629513  19.00  19.0   
443   다사640488  13.00  13.0   
517   다사629512  11.00  11.0   
561   다사616491    N/A   0.0   
564   다사630489  12.00  12.0   
589   다사634490  15.00  15.0   
613   다사638511  12.00  12.0   
642   다사629518    N/A   0.0   
683   다사633493  28.00  28.0   
728   다사644491  40.00  40.0   
831   다사638507  35.00  35.0   
849   다사624480  19.00  19.0   
859   다사633478   6.00   6.0   
885   다사635520   9.00   9.0   
891   다사636497  72.00  72.0   
1478  다사628487   None   NaN   
1583  다사633518   None   NaN   
1602  다사616480   None   NaN   

                                               geometry  \
107   POLYGON ((208170.237 449805.911, 208169.705 44...   
214   POLYGON ((206578.688 448096.771, 206578.156 44...   
252   POLYGON ((205376.118 448490.536, 205375.586 44...   
262   POLYGON ((206364.782 450696.666, 206364.25 450...   
335   POLYGON ((207378.451 448201.062, 207377.92 448...   
344   POLYGON ((207764.236 450904.19, 207763.703 451...   
396   POLYGON ((207062.38 451200.576, 207061.848 451...   
443   POLYGON ((208176.088 448705.503, 208175.556 44...   
517   POLYGON ((207062.912 451100.539, 207062.38 451...   
561   POLYGON ((205773.606 448992.847, 205773.074 44...   
564   POLYGON ((207175.186 448800.221, 207174.654 44...   
589   POLYGON ((207574.802 448902.385, 207574.27 449...   
613   POLYGON ((207963.777 451005.291, 207963.245 45...   
642   POLYGON ((207059.719 451700.761, 207059.187 45...   
683   POLYGON ((207473.169 449201.964, 207472.637 44...   
728   POLYGON ((208574.641 449007.742, 208574.109 44...   
831   POLYGON ((207965.906 450605.143, 207965.374 45...   
849   POLYGON ((206579.751 447896.697, 206579.22 447...   
859   POLYGON ((207481.148 447701.409, 207480.616 44...   
885   POLYGON ((207658.876 451904.028, 207658.344 45...   
891   POLYGON ((207771.153 449603.708, 207770.621 44...   
1478  POLYGON ((206976.176 448599.083, 206975.644 44...   
1583  POLYGON ((207459.867 451702.89, 207459.335 451...   
1602  POLYGON ((205779.456 447892.442, 205778.925 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  
107   POINT (208219.989 449856.195)     0.0    0.0       1.0  
214    POINT (206628.44 448147.055)     0.0    0.0       1.0  
252     POINT (205425.87 448540.82)     0.0    0.0       1.0  
262   POINT (206414.535 450746.951)     0.0    1.0       1.0  
335   POINT (207428.204 448251.347)     0.0    0.0       3.0  
344   POINT (207813.988 450954.475)     0.0    0.0       1.0  
396    POINT (207112.132 451250.86)     0.0    0.0       1.0  
443   POINT (208225.841 448755.787)     0.0    0.0       1.0  
517   POINT (207112.665 451150.823)     0.0    0.0       1.0  
561   POINT (205823.358 449043.132)     0.0    0.0       1.0  
564   POINT (207224.939 448850.505)     0.0    0.0       1.0  
589    POINT (207624.555 448952.67)     0.0    0.0       2.0  
613    POINT (208013.53 451055.576)     0.0    0.0       1.0  
642   POINT (207109.471 451751.045)     0.0    0.0       2.0  
683   POINT (207522.922 449252.249)     0.0    0.0       1.0  
728   POINT (208624.394 449058.026)     0.0    0.0       1.0  
831   POINT (208015.659 450655.428)     0.0    0.0       2.0  
849   POINT (206629.504 447946.981)     0.0    0.0       1.0  
859     POINT (207530.9 447751.694)     0.0    0.0       1.0  
885   POINT (207708.629 451954.313)     0.0    0.0       1.0  
891   POINT (207820.905 449653.993)     0.0    0.0       1.0  
1478  POINT (207025.929 448649.367)     0.0    0.0       1.0  
1583  POINT (207509.619 451753.174)     0.0    0.0       3.0  
1602  POINT (205829.209 447942.727)     0.0    0.0       1.0

## 4.키즈카페

In [ ]:
df_kids_cafes = pd.read_csv('9키즈카페.csv')
df_kids_cafes.head(2)

Unnamed: 0                          시설명               기본주소         위도  \
0          23              서울형키즈카페 시립 팔각당점  서울특별시 광진구 능동로 216  37.549857   
1          25  서울형 키즈카페 자양4동 2호점(꾸미팡팡 놀이터)   서울특별시 광진구 능동로 87  37.539160   

           경도  
0  127.082471  
1  127.069640

In [ ]:
geometry = [Point(xy) for xy in zip(df_kids_cafes['경도'], df_kids_cafes['위도'])]
gdf_kids_cafes = gpd.GeoDataFrame(df_kids_cafes, geometry=geometry, crs='EPSG:4326')

gdf_kids_cafes = gdf_kids_cafes.to_crs(epsg=5181)

# 좌표계 통일
gdf_kids_cafes = gdf_kids_cafes.to_crs(grid_gdf_child_parks.crs)

# 키즈카페 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_kids_cafes, grid_gdf_child_parks, how='left', predicate='within')

# 각 격자 ID별 키즈카페 수 계산
kids_cafes_counts = gdf_joined.groupby('index_right').size()

# 격자에 매핑
grid_gdf_child_parks['키즈카페_수'] = grid_gdf_child_parks.index.map(kids_cafes_counts).fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['키즈카페_수'] != 0]

gid   lbl  val                                           geometry  \
587   다사619489   N/A  0.0  POLYGON ((206074.78 448794.37, 206074.248 4488...   
915   다사616479  None  NaN  POLYGON ((205779.988 447792.406, 205779.456 44...   
1461  다사631501  None  NaN  POLYGON ((207268.839 450001.196, 207268.307 45...   
1583  다사633518  None  NaN  POLYGON ((207459.867 451702.89, 207459.335 451...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  
587   POINT (206124.533 448844.654)     0.0    0.0       0.0     2.0  
915    POINT (205829.741 447842.69)     0.0    0.0       0.0     1.0  
1461  POINT (207318.592 450051.481)     0.0    0.0       0.0     1.0  
1583  POINT (207509.619 451753.174)     0.0    0.0       3.0     1.0

## 5.청소년 유해업소·구역

*   유흥주점
*   단란주점

*   노래연습장
*   비디오물감상실

*  일반게임제공업
*  복합유통게임제공업

In [ ]:
df_hazardous_facilities = pd.read_csv('4청소년 유해시설(업종추가).csv')
df_hazardous_facilities.tail(2)

Unnamed: 0      사업장명 상세영업상태명                         지번주소        업종명  \
385         385  Fun City     영업중  서울특별시 광진구 화양동 9-91 캠퍼스 프라자   복합유통게임제공업   
386         386     쌈바플스방     영업중        서울특별시 광진구 화양동 3-37번지   복합유통게임제공업   

            위도          경도  
385  37.541510  127.068690  
386  37.542692  127.071605

In [ ]:
geometry = [Point(xy) for xy in zip(df_hazardous_facilities['경도'], df_hazardous_facilities['위도'])]
gdf_hazardous_facilities = gpd.GeoDataFrame(df_hazardous_facilities, geometry=geometry, crs='EPSG:4326')

gdf_hazardous_facilities = gdf_hazardous_facilities.to_crs(epsg=5181)

# 좌표계 통일
gdf_hazardous_facilities = gdf_hazardous_facilities.to_crs(grid_gdf_child_parks.crs)

# 유해시설 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_hazardous_facilities, grid_gdf_child_parks, how='left', predicate='within')

# 각 격자 ID별 유해시설 수 계산
hazardous_facilities_counts = gdf_joined.groupby('index_right').size()

# 격자에 매핑
grid_gdf_child_parks['청소년유해업소_수'] = grid_gdf_child_parks.index.map(hazardous_facilities_counts).fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['청소년유해업소_수'] != 0]

gid    lbl   val  \
7     다사621498  12.00  12.0   
10    다사634513  26.00  26.0   
13    다사622499    N/A   0.0   
23    다사626509  10.00  10.0   
24    다사630520  11.00  11.0   
...        ...    ...   ...   
1684  다사623498   None   NaN   
1729  다사625497   None   NaN   
1769  다사617491   None   NaN   
1785  다사642491   None   NaN   
1797  다사631485   None   NaN   

                                               geometry  \
7     POLYGON ((206270.066 449695.765, 206269.534 44...   
10    POLYGON ((207562.565 451203.237, 207562.033 45...   
13    POLYGON ((206369.571 449796.334, 206369.039 44...   
23    POLYGON ((206764.398 450798.832, 206763.866 45...   
24    POLYGON ((207158.691 451901.367, 207158.159 45...   
...                                                 ...   
1684  POLYGON ((206470.14 449696.829, 206469.608 449...   
1729  POLYGON ((206670.746 449597.856, 206670.214 44...   
1769  POLYGON ((205873.643 448993.379, 205873.111 44...   
1785  POLYGON ((208374.567 449006.678, 208374.035 44...   
1797  POLYGON ((207277.351 448400.605, 207276.819 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
7      POINT (206319.819 449746.05)     0.0    0.0       0.0     0.0   
10    POINT (207612.317 451253.521)     0.0    0.0       0.0     0.0   
13    POINT (206419.323 449846.619)     0.0    0.0       0.0     0.0   
23     POINT (206814.15 450849.116)     0.0    0.0       0.0     0.0   
24    POINT (207208.444 451951.652)     0.0    0.0       0.0     0.0   
...                             ...     ...    ...       ...     ...   
1684  POINT (206519.892 449747.114)     0.0    0.0       0.0     0.0   
1729  POINT (206720.498 449648.141)     0.0    0.0       0.0     0.0   
1769  POINT (205923.395 449043.664)     0.0    0.0       0.0     0.0   
1785  POINT (208424.319 449056.962)     0.0    0.0       0.0     0.0   
1797  POINT (207327.103 448450.889)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  
7           2.0  
10          1.0  
13          2.0  
23          3.0  
24          2.0  
...         ...  
1684        5.0  
1729        1.0  
1769        1.0  
1785        2.0  
1797        3.0  

[180 rows x 10 columns]

## 6.공영주차장

In [ ]:
df_public_parking_lot = pd.read_csv('13주차장.csv')
df_public_parking_lot = df_public_parking_lot[df_public_parking_lot['위도'].notna()]
df_public_parking_lot.isna().sum()

Unnamed: 0    0
ID            0
주차장명          0
주차장유형         0
지번주소          0
위도            0
경도            0
dtype: int64

In [ ]:
geometry = [Point(xy) for xy in zip(df_public_parking_lot['경도'], df_public_parking_lot['위도'])]
gdf_public_parking_lot = gpd.GeoDataFrame(df_public_parking_lot, geometry=geometry, crs='EPSG:4326')

gdf_public_parking_lot = gdf_public_parking_lot.to_crs(epsg=5181)

# 좌표계 통일
gdf_public_parking_lot = gdf_public_parking_lot.to_crs(grid_gdf_child_parks.crs)

# 주차장 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_public_parking_lot, grid_gdf_child_parks, how='left', predicate='within')

# 각 격자 ID별 주차장 수 계산
public_parking_lot_counts = gdf_joined.groupby('index_right').size()

# 격자에 매핑
grid_gdf_child_parks['공영주차장_수'] = grid_gdf_child_parks.index.map(public_parking_lot_counts).fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['공영주차장_수'] != 0]

gid    lbl   val  \
10    다사634513  26.00  26.0   
27    다사625484  27.00  27.0   
125   다사633523  24.00  24.0   
169   다사629506  18.00  18.0   
374   다사640504  30.00  30.0   
435   다사629522  21.00  21.0   
456   다사618489    N/A   0.0   
463   다사621496   8.00   8.0   
524   다사614483  20.00  20.0   
545   다사638483  17.00  17.0   
608   다사638489  10.00  10.0   
617   다사635488   9.00   9.0   
851   다사637509  16.00  16.0   
969   다사623499   None   NaN   
973   다사626478   None   NaN   
1298  다사639482   None   NaN   

                                               geometry  \
10    POLYGON ((207562.565 451203.237, 207562.033 45...   
27    POLYGON ((206677.661 448297.376, 206677.129 44...   
125   POLYGON ((207457.206 452203.075, 207456.673 45...   
169   POLYGON ((207066.105 450500.317, 207065.573 45...   
374   POLYGON ((208167.576 450306.096, 208167.044 45...   
435   POLYGON ((207057.59 452100.909, 207057.058 452...   
456   POLYGON ((205974.743 448793.838, 205974.211 44...   
463   POLYGON ((206271.13 449495.692, 206270.598 449...   
524   POLYGON ((205577.787 448191.489, 205577.255 44...   
545   POLYGON ((207978.674 448204.254, 207978.142 44...   
608   POLYGON ((207975.482 448804.476, 207974.95 448...   
617   POLYGON ((207675.903 448702.843, 207675.371 44...   
851   POLYGON ((207864.805 450804.685, 207864.273 45...   
969   POLYGON ((206469.608 449796.866, 206469.076 44...   
973   POLYGON ((206780.889 447697.687, 206780.357 44...   
1298  POLYGON ((208079.243 448104.748, 208078.711 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
10    POINT (207612.317 451253.521)     0.0    0.0       0.0     0.0   
27    POINT (206727.413 448347.661)     0.0    1.0       0.0     0.0   
125   POINT (207506.958 452253.359)     0.0    0.0       0.0     0.0   
169   POINT (207115.857 450550.602)     0.0    0.0       0.0     0.0   
374   POINT (208217.329 450356.381)     0.0    0.0       0.0     0.0   
435   POINT (207107.342 452151.193)     0.0    0.0       0.0     0.0   
456   POINT (206024.496 448844.122)     0.0    0.0       0.0     0.0   
463   POINT (206320.883 449545.976)     0.0    0.0       0.0     0.0   
524    POINT (205627.54 448241.773)     0.0    0.0       0.0     0.0   
545   POINT (208028.426 448254.538)     0.0    0.0       0.0     0.0   
608    POINT (208025.235 448854.76)     0.0    0.0       0.0     0.0   
617   POINT (207725.656 448753.128)     0.0    0.0       0.0     0.0   
851    POINT (207914.557 450854.97)     0.0    0.0       0.0     0.0   
969    POINT (206519.36 449847.151)     0.0    0.0       0.0     0.0   
973   POINT (206830.641 447747.971)     0.0    0.0       0.0     0.0   
1298  POINT (208128.995 448155.033)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  공영주차장_수  
10          1.0      1.0  
27          0.0      1.0  
125         0.0      1.0  
169         0.0      1.0  
374         0.0      1.0  
435         0.0      1.0  
456         0.0      1.0  
463         0.0      1.0  
524         0.0      1.0  
545         1.0      1.0  
608         0.0      1.0  
617         3.0      1.0  
851         0.0      1.0  
969         0.0      1.0  
973         0.0      1.0  
1298        0.0      1.0

## 7.노인복지시설

In [ ]:
df_senior_welfare_facilities = pd.read_csv('11노인복지(결측값 삭제).csv')
# df_senior_welfare_facilities = df_senior_welfare_facilities[df_senior_welfare_facilities['위도'].notna()]
# 또는 df_senior_welfare_facilities = df_senior_welfare_facilities.dropna(subset=['위도']) 로 '11노인복지.csv'의 결측값을 삭제하고 저장하였음
df_senior_welfare_facilities.isna().sum()

Unnamed: 0     0
시설명            0
시설주소           0
시설종류명(시설유형)    0
위도             0
경도             0
dtype: int64

In [ ]:
geometry = [Point(xy) for xy in zip(df_senior_welfare_facilities['경도'], df_senior_welfare_facilities['위도'])]
gdf_senior_welfare_facilities = gpd.GeoDataFrame(df_senior_welfare_facilities, geometry=geometry, crs='EPSG:4326')

gdf_senior_welfare_facilities = gdf_senior_welfare_facilities.to_crs(epsg=5181)

# 좌표계 통일
gdf_senior_welfare_facilities = gdf_senior_welfare_facilities.to_crs(grid_gdf_child_parks.crs)

# 노인복지시설 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_senior_welfare_facilities, grid_gdf_child_parks, how='left', predicate='within')

# 각 격자 ID별 노인복지시설 수 계산
senior_welfare_facilities_counts = gdf_joined.groupby('index_right').size()

# 격자에 매핑
grid_gdf_child_parks['노인복지시설_수'] = grid_gdf_child_parks.index.map(senior_welfare_facilities_counts).fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['노인복지시설_수'] != 0]

gid    lbl   val  \
8     다사618486  85.00  85.0   
14    다사640491  42.00  42.0   
56    다사636506    N/A   0.0   
62    다사637498  42.00  42.0   
79    다사644502   6.00   6.0   
...        ...    ...   ...   
1110  다사638495   None   NaN   
1267  다사622504   None   NaN   
1415  다사639484   None   NaN   
1442  다사643486   None   NaN   
1564  다사641490   None   NaN   

                                               geometry  \
8     POLYGON ((205976.339 448493.727, 205975.807 44...   
14    POLYGON ((208174.493 449005.614, 208173.961 44...   
56    POLYGON ((207766.364 450504.042, 207765.832 45...   
62    POLYGON ((207870.658 449704.278, 207870.126 44...   
79    POLYGON ((208568.789 450108.15, 208568.257 450...   
...                                                 ...   
1110  POLYGON ((207972.291 449404.698, 207971.759 44...   
1267  POLYGON ((206366.911 450296.519, 206366.379 45...   
1415  POLYGON ((208078.179 448304.823, 208077.647 44...   
1442  POLYGON ((208477.264 448507.024, 208476.732 44...   
1564  POLYGON ((208275.062 448906.109, 208274.53 449...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
8     POINT (206026.091 448544.011)     0.0    0.0       0.0     0.0   
14    POINT (208224.245 449055.899)     0.0    0.0       0.0     0.0   
56    POINT (207816.117 450554.326)     0.0    0.0       0.0     0.0   
62     POINT (207920.41 449754.562)     0.0    0.0       0.0     0.0   
79    POINT (208618.542 450158.435)     0.0    0.0       0.0     0.0   
...                             ...     ...    ...       ...     ...   
1110  POINT (208022.043 449454.983)     0.0    0.0       0.0     0.0   
1267  POINT (206416.663 450346.803)     1.0    0.0       0.0     0.0   
1415  POINT (208127.931 448355.107)     0.0    0.0       0.0     0.0   
1442  POINT (208527.016 448557.309)     0.0    0.0       0.0     0.0   
1564  POINT (208324.814 448956.393)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  공영주차장_수  노인복지시설_수  
8           0.0      0.0       1.0  
14          0.0      0.0       1.0  
56          2.0      0.0       1.0  
62          0.0      0.0       1.0  
79          0.0      0.0       1.0  
...         ...      ...       ...  
1110        1.0      0.0       2.0  
1267        0.0      0.0       1.0  
1415        0.0      0.0       2.0  
1442        0.0      0.0       1.0  
1564        0.0      0.0       1.0  

[67 rows x 12 columns]

## 8.공시지가




In [ ]:
path = '/content/drive/MyDrive/광진구 공모전 DB/광진구 공모전 데이터/db/2광진구_공시지가_100/nlsp_021004001.shp'

# 좌표계 변환
gdf_land_price = gpd.read_file(path).to_crs(epsg=5181)

# 컬럼명 변경
gdf_land_price = gdf_land_price.rename(columns={'val': '공시지가'})

gdf_land_price.head(2)

gid         lbl        공시지가  \
0  ë¤ì¬629496  5658798.87  5658798.87   
1  ë¤ì¬636494  4395647.73  4395647.73   

                                            geometry  
0  POLYGON ((207071.426 449499.947, 207070.894 44...  
1  POLYGON ((207772.749 449303.597, 207772.217 44...

### 최종 코드

In [ ]:
# ★★ 참고사항 반영하여 정리한 격자 전체 Polygon(geometry) 기준 spatial join
# 1. Spatial Join
grid_land_price = gpd.sjoin(
    grid_gdf_child_parks[['geometry']],
    gdf_land_price[['geometry', '공시지가']],
    how='left',
    predicate='intersects')

# 2. 겹친 필지의 평균 공시지가 계산 (단일/다중 모두 포함)
mean_by_idx = grid_land_price.groupby(grid_land_price.index)['공시지가'].mean()

# 3. 평균 공시지가를 매핑
# - 격자 인덱스를 기준으로 mean_by_idx에서 값을 가져오고,
# - 매핑되지 않은 경우는 0으로 처리
grid_gdf_child_parks['공시지가'] = grid_gdf_child_parks.index.map(mean_by_idx).fillna(0)

### 최종 결과

In [ ]:
grid_gdf_child_parks[grid_gdf_child_parks['공시지가'] != 0]

gid    lbl   val  \
0     다사633494  15.00  15.0   
1     다사626517  18.00  18.0   
2     다사642512  30.00  30.0   
3     다사647489  71.00  71.0   
4     다사640506  23.00  23.0   
...        ...    ...   ...   
1806  다사610477   None   NaN   
1807  다사636487   None   NaN   
1809  다사624501   None   NaN   
1810  다사613479   None   NaN   
1811  다사630474   None   NaN   

                                               geometry  \
0     POLYGON ((207472.637 449302.001, 207472.105 44...   
1     POLYGON ((206760.14 451599.127, 206759.608 451...   
2     POLYGON ((208363.394 451107.457, 208362.861 45...   
3     POLYGON ((208875.816 448809.263, 208875.284 44...   
4     POLYGON ((208166.512 450506.17, 208165.98 4506...   
...                                                 ...   
1806  POLYGON ((205180.831 447589.141, 205180.299 44...   
1807  POLYGON ((207776.472 448603.338, 207775.94 448...   
1809  POLYGON ((206568.581 449997.472, 206568.049 45...   
1810  POLYGON ((205479.878 447790.81, 205479.346 447...   
1811  POLYGON ((207183.164 447299.666, 207182.632 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
0      POINT (207522.39 449352.286)     0.0    1.0       0.0     0.0   
1     POINT (206809.893 451649.412)     0.0    0.0       0.0     0.0   
2     POINT (208413.146 451157.742)     0.0    0.0       0.0     0.0   
3     POINT (208925.569 448859.548)     0.0    0.0       0.0     0.0   
4     POINT (208216.265 450556.455)     0.0    0.0       0.0     0.0   
...                             ...     ...    ...       ...     ...   
1806  POINT (205230.584 447639.425)     0.0    0.0       0.0     0.0   
1807  POINT (207826.225 448653.623)     0.0    0.0       0.0     0.0   
1809  POINT (206618.333 450047.757)     0.0    0.0       0.0     0.0   
1810   POINT (205529.63 447841.094)     0.0    0.0       0.0     0.0   
1811   POINT (207232.916 447349.95)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  공영주차장_수  노인복지시설_수          공시지가  
0           0.0      0.0       0.0  4.801408e+06  
1           0.0      0.0       0.0  2.813924e+06  
2           0.0      0.0       0.0  1.109825e+06  
3           0.0      0.0       0.0  2.578754e+06  
4           0.0      0.0       0.0  3.854859e+06  
...         ...      ...       ...           ...  
1806        0.0      0.0       0.0  4.466000e+05  
1807        0.0      0.0       0.0  5.825167e+06  
1809        0.0      0.0       0.0  3.047138e+06  
1810        0.0      0.0       0.0  4.465999e+05  
1811        0.0      0.0       0.0  4.465999e+05  

[1687 rows x 13 columns]

## 9.유소년 인구

In [ ]:
path = '/content/drive/MyDrive/광진구 공모전 DB/광진구 공모전 데이터/db/1광진구_유소년_인구수_100/nlsp_021001004.shp'

# 좌표계 변환
gdf_youth_population = gpd.read_file(path).to_crs(epsg=5181)

# 유소년 인구 컬럼 확인 (['gid', 'lbl', 'val', 'geometry'] = ['Geo ID', '지역 이름 또는 격자 ID 등 Label', '유소년 인구 수 Value', 'Polygon'])
gdf_youth_population.columns

# 유소년 인구 컬럼명 변경
gdf_youth_population = gdf_youth_population.rename(columns={'val': '유소년_인구수'})
gdf_youth_population[['유소년_인구수', 'geometry']]

유소년_인구수                                           geometry
0        15.0  POLYGON ((207472.637 449302.001, 207472.105 44...
1        18.0  POLYGON ((206760.14 451599.127, 206759.608 451...
2        30.0  POLYGON ((208363.394 451107.457, 208362.861 45...
3        71.0  POLYGON ((208875.816 448809.263, 208875.284 44...
4        23.0  POLYGON ((208166.512 450506.17, 208165.98 4506...
...       ...                                                ...
1807      NaN  POLYGON ((207776.472 448603.338, 207775.94 448...
1808      NaN  POLYGON ((208556.016 452509.041, 208555.484 45...
1809      NaN  POLYGON ((206568.581 449997.472, 206568.049 45...
1810      NaN  POLYGON ((205479.878 447790.81, 205479.346 447...
1811      NaN  POLYGON ((207183.164 447299.666, 207182.632 44...

[1812 rows x 2 columns]

In [ ]:
# 격자 데이터(grid_gdf_child_parks)에 유소년 인구 매핑 (intersects or within)

# 격자 중심점 생성
grid_gdf_child_parks['centroid'] = grid_gdf_child_parks.geometry.centroid
centroid_gdf = gpd.GeoDataFrame(grid_gdf_child_parks[['centroid']], geometry='centroid', crs='EPSG:5181')

# Spatial Join: 격자 중심점이 포함된 유소년 인구 격자 찾아서 인구수 붙이기
grid_youth_population = gpd.sjoin(centroid_gdf, gdf_youth_population[['geometry', '유소년_인구수']], how='left', predicate='intersects')

# 유소년 인구 수 컬럼을 원래 격자와 merge
grid_gdf_child_parks['유소년_인구수'] = grid_youth_population['유소년_인구수'].fillna(0)

# 결과 확인
grid_gdf_child_parks

gid    lbl   val  \
0     다사633494  15.00  15.0   
1     다사626517  18.00  18.0   
2     다사642512  30.00  30.0   
3     다사647489  71.00  71.0   
4     다사640506  23.00  23.0   
...        ...    ...   ...   
1807  다사636487   None   NaN   
1808  다사644526   None   NaN   
1809  다사624501   None   NaN   
1810  다사613479   None   NaN   
1811  다사630474   None   NaN   

                                               geometry  \
0     POLYGON ((207472.637 449302.001, 207472.105 44...   
1     POLYGON ((206760.14 451599.127, 206759.608 451...   
2     POLYGON ((208363.394 451107.457, 208362.861 45...   
3     POLYGON ((208875.816 448809.263, 208875.284 44...   
4     POLYGON ((208166.512 450506.17, 208165.98 4506...   
...                                                 ...   
1807  POLYGON ((207776.472 448603.338, 207775.94 448...   
1808  POLYGON ((208556.016 452509.041, 208555.484 45...   
1809  POLYGON ((206568.581 449997.472, 206568.049 45...   
1810  POLYGON ((205479.878 447790.81, 205479.346 447...   
1811  POLYGON ((207183.164 447299.666, 207182.632 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
0      POINT (207522.39 449352.286)     0.0    1.0       0.0     0.0   
1     POINT (206809.893 451649.412)     0.0    0.0       0.0     0.0   
2     POINT (208413.146 451157.742)     0.0    0.0       0.0     0.0   
3     POINT (208925.569 448859.548)     0.0    0.0       0.0     0.0   
4     POINT (208216.265 450556.455)     0.0    0.0       0.0     0.0   
...                             ...     ...    ...       ...     ...   
1807  POINT (207826.225 448653.623)     0.0    0.0       0.0     0.0   
1808  POINT (208605.769 452559.326)     0.0    0.0       0.0     0.0   
1809  POINT (206618.333 450047.757)     0.0    0.0       0.0     0.0   
1810   POINT (205529.63 447841.094)     0.0    0.0       0.0     0.0   
1811   POINT (207232.916 447349.95)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  공영주차장_수  노인복지시설_수          공시지가  유소년_인구수  
0           0.0      0.0       0.0  4.801408e+06     15.0  
1           0.0      0.0       0.0  2.813924e+06     18.0  
2           0.0      0.0       0.0  1.109825e+06     30.0  
3           0.0      0.0       0.0  2.578754e+06     71.0  
4           0.0      0.0       0.0  3.854859e+06     23.0  
...         ...      ...       ...           ...      ...  
1807        0.0      0.0       0.0  5.825167e+06      0.0  
1808        0.0      0.0       0.0  0.000000e+00      0.0  
1809        0.0      0.0       0.0  3.047138e+06      0.0  
1810        0.0      0.0       0.0  4.465999e+05      0.0  
1811        0.0      0.0       0.0  4.465999e+05      0.0  

[1812 rows x 14 columns]

## 10.노인 인구

In [ ]:
path = '/content/drive/MyDrive/광진구 공모전 DB/광진구 공모전 데이터/db/5광진구_고령자_인구수_100/nlsp_021001010.shp'

# 좌표계 변환
gdf_senior_population = gpd.read_file(path).to_crs(epsg=5181)

# 컬럼 확인
gdf_senior_population.columns
gdf_senior_population = gdf_senior_population.rename(columns={'val': '노인_인구수'})

# Spatial Join
centroids_gdf = gpd.GeoDataFrame(grid_gdf_child_parks[['centroid']], geometry='centroid', crs='EPSG:5181')
grid_senior_population = gpd.sjoin(centroids_gdf, gdf_senior_population[['geometry', '노인_인구수']], how='left', predicate='intersects')

# 원래 격자와 merge
grid_gdf_child_parks['노인_인구수'] = grid_senior_population['노인_인구수'].fillna(0)

# 결과 확인
grid_gdf_child_parks[grid_gdf_child_parks['노인_인구수'] != 0]

gid    lbl   val  \
0     다사633494  15.00  15.0   
1     다사626517  18.00  18.0   
2     다사642512  30.00  30.0   
3     다사647489  71.00  71.0   
4     다사640506  23.00  23.0   
...        ...    ...   ...   
1684  다사623498   None   NaN   
1742  다사635505   None   NaN   
1769  다사617491   None   NaN   
1795  다사620494   None   NaN   
1797  다사631485   None   NaN   

                                               geometry  \
0     POLYGON ((207472.637 449302.001, 207472.105 44...   
1     POLYGON ((206760.14 451599.127, 206759.608 451...   
2     POLYGON ((208363.394 451107.457, 208362.861 45...   
3     POLYGON ((208875.816 448809.263, 208875.284 44...   
4     POLYGON ((208166.512 450506.17, 208165.98 4506...   
...                                                 ...   
1684  POLYGON ((206470.14 449696.829, 206469.608 449...   
1742  POLYGON ((207666.859 450403.473, 207666.327 45...   
1769  POLYGON ((205873.643 448993.379, 205873.111 44...   
1795  POLYGON ((206172.157 449295.086, 206171.625 44...   
1797  POLYGON ((207277.351 448400.605, 207276.819 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
0      POINT (207522.39 449352.286)     0.0    1.0       0.0     0.0   
1     POINT (206809.893 451649.412)     0.0    0.0       0.0     0.0   
2     POINT (208413.146 451157.742)     0.0    0.0       0.0     0.0   
3     POINT (208925.569 448859.548)     0.0    0.0       0.0     0.0   
4     POINT (208216.265 450556.455)     0.0    0.0       0.0     0.0   
...                             ...     ...    ...       ...     ...   
1684  POINT (206519.892 449747.114)     0.0    0.0       0.0     0.0   
1742  POINT (207716.612 450453.757)     0.0    0.0       0.0     0.0   
1769  POINT (205923.395 449043.664)     0.0    0.0       0.0     0.0   
1795    POINT (206221.91 449345.37)     0.0    0.0       0.0     0.0   
1797  POINT (207327.103 448450.889)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  공영주차장_수  노인복지시설_수          공시지가  유소년_인구수  노인_인구수  
0           0.0      0.0       0.0  4.801408e+06     15.0    47.0  
1           0.0      0.0       0.0  2.813924e+06     18.0    48.0  
2           0.0      0.0       0.0  1.109825e+06     30.0   101.0  
3           0.0      0.0       0.0  2.578754e+06     71.0    26.0  
4           0.0      0.0       0.0  3.854859e+06     23.0   116.0  
...         ...      ...       ...           ...      ...     ...  
1684        5.0      0.0       0.0  6.222092e+06      0.0     7.0  
1742        0.0      0.0       0.0  5.267737e+06      0.0    14.0  
1769        1.0      0.0       0.0  7.431700e+06      0.0    31.0  
1795        0.0      0.0       0.0  5.810347e+06      0.0    30.0  
1797        3.0      0.0       0.0  5.951051e+06      0.0    35.0  

[921 rows x 15 columns]

# 시각화(중간 결과 확인)

In [ ]:
import folium
import geopandas as gpd
import branca.colormap as cm

# 지도 초기화
map_center = [37.5386, 127.082]
m = folium.Map(location=map_center, zoom_start=14, tiles='cartodbpositron')

# ------------------- 유소년 인구 격자 -------------------
youth_layer = folium.FeatureGroup(name='🟧 유소년 인구수 격자', show=True)
col_youth = '유소년_인구수'
colormap_youth = cm.linear.YlOrRd_09.scale(
    grid_gdf_child_parks[col_youth].min(),
    grid_gdf_child_parks[col_youth].max()
)
colormap_youth.caption = '격자별 유소년 인구수'
colormap_youth.add_to(m)

grid_gdf_viz = grid_gdf_child_parks.drop(columns=['centroid'])
folium.GeoJson(
    grid_gdf_viz,
    style_function=lambda f: {
        'fillColor': colormap_youth(f['properties'][col_youth]),
        'color': 'gray',
        'weight': 0.3,
        'fillOpacity': 0.6,
    },
    tooltip=folium.GeoJsonTooltip(fields=[col_youth], aliases=['유소년 인구수'])
).add_to(youth_layer)
youth_layer.add_to(m)

# ------------------- 노인 인구 격자 -------------------
senior_layer = folium.FeatureGroup(name='🟥 노인 인구수 격자', show=False)
col_senior = '노인_인구수'
colormap_senior = cm.linear.PuBuGn_09.scale(
    grid_gdf_child_parks[col_senior].min(),
    grid_gdf_child_parks[col_senior].max()
)
colormap_senior.caption = '격자별 노인 인구수'
colormap_senior.add_to(m)

folium.GeoJson(
    grid_gdf_viz,
    style_function=lambda f: {
        'fillColor': colormap_senior(f['properties'][col_senior]),
        'color': 'gray',
        'weight': 0.3,
        'fillOpacity': 0.6,
    },
    tooltip=folium.GeoJsonTooltip(fields=[col_senior], aliases=['노인 인구수'])
).add_to(senior_layer)
senior_layer.add_to(m)

# ------------------- 기타 유아시설 -------------------
facilities = [
    (gdf_elementary_schools, '🟡 초등학교', '#ffd700'),
    (gdf_kindergartens, '🧡 유치원', '#ffa500'),
    (gdf_kids_cafes, '🧩 키즈카페', '#ff69b4'),
    (gdf_child_centers, '🧒 지역아동센터', '#9370db')
]

for gdf, name, color in facilities:
    layer = folium.FeatureGroup(name=name, show=False)
    gdf = gdf.to_crs(epsg=4326)
    for _, row in gdf.iterrows():
        folium.CircleMarker(
            location=[row.geometry.y, row.geometry.x],
            radius=4, color=color, fill_color=color,
            fill=True, fill_opacity=0.9,
            popup=row.get('시설명', name.split()[-1])
        ).add_to(layer)
    layer.add_to(m)

# ------------------- 레이어 컨트롤 -------------------
folium.LayerControl(collapsed=False).add_to(m)

# ------------------- 지도 출력 -------------------
m

## 11.인근 공원

In [ ]:
df_parks = pd.read_csv('3어린이공원.csv')
df_parks.tail(2)

Unnamed: 0         공원명 공원구분               소재지지번주소 세부행정동         위도  \
41          41  중곡역소공원(가칭)  소공원   서울특별시 광진구 중곡동 30-79  중곡3동  37.565878   
42          42   신양소공원(가칭)  소공원  서울특별시 광진구 자양동 510-38  자양4동  37.536990   

            경도    공원면적 공원보유시설(운동시설)   공원보유시설(유희시설)  공원보유시설(교양시설) 공원보유시설(기타시설)  
41  127.084911  1276.7          NaN  조합놀이대, 흔들놀이기구           NaN          NaN  
42  127.068941   310.2          NaN            NaN           NaN          NaN

### 최종 코드

In [ ]:
geometry = [Point(xy) for xy in zip(df_parks['경도'], df_parks['위도'])]
gdf_parks = gpd.GeoDataFrame(df_parks, geometry=geometry, crs='EPSG:4326')

gdf_parks = gdf_parks.to_crs(epsg=5181)

# 좌표계 통일
gdf_parks = gdf_parks.to_crs(grid_gdf_child_parks.crs)

# 공원 포인트 → 격자와 공간조인
gdf_joined = gpd.sjoin(gdf_parks, grid_gdf_child_parks, how='left', predicate='within')

# 각 격자 ID별 공원 수 계산
parks_counts = gdf_joined.groupby('index_right').size()

# 격자에 매핑
grid_gdf_child_parks['인근공원_수'] = grid_gdf_child_parks.index.map(parks_counts).fillna(0)


grid_gdf_child_parks[grid_gdf_child_parks['인근공원_수'] != 0]

gid    lbl   val  \
18    다사642507  52.00  52.0   
36    다사633519    N/A   0.0   
83    다사619487  94.00  94.0   
94    다사618484    N/A   0.0   
112   다사639499  29.00  29.0   
113   다사629521  28.00  28.0   
118   다사638493  36.00  36.0   
174   다사627482  12.00  12.0   
193   다사628517  47.00  47.0   
202   다사634492  22.00  22.0   
252   다사612486   8.00   8.0   
260   다사621497   7.00   7.0   
342   다사619483  49.00  49.0   
351   다사641491  13.00  13.0   
366   다사631504  32.00  32.0   
388   다사623481  24.00  24.0   
390   다사617493  13.00  13.0   
409   다사622506   8.00   8.0   
423   다사639488  31.00  31.0   
436   다사623508  26.00  26.0   
456   다사618489    N/A   0.0   
473   다사620495    N/A   0.0   
508   다사637486    N/A   0.0   
528   다사631479  30.00  30.0   
534   다사632512  22.00  22.0   
546   다사635481  10.00  10.0   
563   다사638491   8.00   8.0   
613   다사638511  12.00  12.0   
618   다사650497  24.00  24.0   
630   다사636480  20.00  20.0   
659   다사627485  16.00  16.0   
745   다사639509  15.00  15.0   
750   다사616482  81.00  81.0   
770   다사619492   6.00   6.0   
806   다사628505   8.00   8.0   
836   다사618497    N/A   0.0   
871   다사630484  21.00  21.0   
884   다사630488    N/A   0.0   
891   다사636497  72.00  72.0   
1023  다사641486   None   NaN   
1024  다사640486   None   NaN   
1347  다사617481   None   NaN   
1445  다사647499   None   NaN   

                                               geometry  \
18    POLYGON ((208366.054 450607.272, 208365.522 45...   
36    POLYGON ((207459.335 451802.927, 207458.802 45...   
83    POLYGON ((206075.844 448594.296, 206075.312 44...   
94    POLYGON ((205977.403 448293.653, 205976.871 44...   
112   POLYGON ((208070.2 449805.379, 208069.668 4499...   
113   POLYGON ((207058.122 452000.872, 207057.59 452...   
118   POLYGON ((207973.355 449204.624, 207972.823 44...   
174   POLYGON ((206878.798 448098.366, 206878.267 44...   
193   POLYGON ((206960.214 451600.192, 206959.682 45...   
202   POLYGON ((207573.738 449102.459, 207573.206 44...   
252   POLYGON ((205376.118 448490.536, 205375.586 44...   
260   POLYGON ((206270.598 449595.728, 206270.066 44...   
342   POLYGON ((206077.971 448194.148, 206077.44 448...   
351   POLYGON ((208274.53 449006.146, 208273.998 449...   
366   POLYGON ((207267.243 450301.307, 207266.711 45...   
388   POLYGON ((206479.183 447996.202, 206478.651 44...   
390   POLYGON ((205872.579 449193.453, 205872.047 44...   
409   POLYGON ((206365.847 450496.592, 206365.314 45...   
423   POLYGON ((208076.051 448704.971, 208075.519 44...   
436   POLYGON ((206464.819 450697.198, 206464.287 45...   
456   POLYGON ((205974.743 448793.838, 205974.211 44...   
473   POLYGON ((206171.625 449395.123, 206171.093 44...   
508   POLYGON ((207877.041 448503.833, 207876.509 44...   
528   POLYGON ((207280.542 447800.383, 207280.01 447...   
534   POLYGON ((207363.023 451102.135, 207362.491 45...   
546   POLYGON ((207679.626 448002.584, 207679.094 44...   
563   POLYGON ((207974.418 449004.55, 207973.887 449...   
613   POLYGON ((207963.777 451005.291, 207963.245 45...   
618   POLYGON ((209171.672 449611.157, 209171.14 449...   
630   POLYGON ((207780.195 447903.079, 207779.663 44...   
659   POLYGON ((206877.203 448398.477, 206876.671 44...   
745   POLYGON ((208064.879 450805.749, 208064.347 45...   
750   POLYGON ((205778.393 448092.516, 205777.861 44...   
770   POLYGON ((206073.184 449094.48, 206072.652 449...   
806   POLYGON ((206966.6 450399.748, 206966.068 4504...   
836   POLYGON ((205970.488 449594.132, 205969.956 44...   
871   POLYGON ((207177.846 448300.036, 207177.314 44...   
884   POLYGON ((207175.718 448700.184, 207175.186 44...   
891   POLYGON ((207771.153 449603.708, 207770.621 44...   
1023  POLYGON ((208277.189 448505.96, 208276.657 448...   
1024  POLYGON ((208177.152 448505.429, 208176.62 448...   
1347  POLYGON ((205878.961 447993.011, 205878.43 448...   
1445  POLYGON ((208870.497 449809.635, 208869.965 44...   

                           centroid  초등학교_수  유치원_

## 12.토지 기울기

In [ ]:
# 1. 파일 불러오기 및 컬럼명 지정
df_slope = pd.read_csv('/content/drive/MyDrive/광진구 공모전 DB/광진구 공모전 데이터/db/수연/광진구_DEM.txt', sep=' ', header=None, names=['x', 'y', 'slope'])

# 2. GeoDataFrame 변환
gdf_slope = gpd.GeoDataFrame(df_slope, geometry=gpd.points_from_xy(df_slope['x'], df_slope['y']), crs='EPSG:5186')  # Raw-Data의 좌표계로 불러와야 함
gdf_slope = gdf_slope.to_crs(grid_gdf_child_parks.crs)  # 좌표계 변환

# Spatial Join: grid_gdf_child_parks의 격자별로 포함된 slope(기울기) 점(값)들을 따로 매칭
grid_slope = gpd.sjoin(grid_gdf_child_parks, gdf_slope, how='left', predicate='intersects')

# 격자별로 각 격자 안에 매칭된 slope 값들의 평균을 구해 '평균 기울기'를 따로 계산
avg_slope = grid_slope.groupby('geometry')['slope'].mean().reset_index()  # .reset_index()가 groupby 결과('geometry'가 index가 됨)를 다시 데이터프레임으로 만들어줌
avg_slope = avg_slope.rename(columns={'slope': '평균_기울기'})

# 계산한 '평균 기울기'를 grid_gdf_child_parks와 merge
grid_gdf_child_parks = grid_gdf_child_parks.merge(avg_slope, on='geometry', how='left')
grid_gdf_child_parks['평균_기울기'] = grid_gdf_child_parks['평균_기울기'].fillna(0)
grid_gdf_child_parks[grid_gdf_child_parks['평균_기울기'] != 0]

gid    lbl   val  \
0     다사633494  15.00  15.0   
1     다사626517  18.00  18.0   
2     다사642512  30.00  30.0   
3     다사647489  71.00  71.0   
4     다사640506  23.00  23.0   
...        ...    ...   ...   
1807  다사636487   None   NaN   
1808  다사644526   None   NaN   
1809  다사624501   None   NaN   
1810  다사613479   None   NaN   
1811  다사630474   None   NaN   

                                               geometry  \
0     POLYGON ((207472.637 449302.001, 207472.105 44...   
1     POLYGON ((206760.14 451599.127, 206759.608 451...   
2     POLYGON ((208363.394 451107.457, 208362.861 45...   
3     POLYGON ((208875.816 448809.263, 208875.284 44...   
4     POLYGON ((208166.512 450506.17, 208165.98 4506...   
...                                                 ...   
1807  POLYGON ((207776.472 448603.338, 207775.94 448...   
1808  POLYGON ((208556.016 452509.041, 208555.484 45...   
1809  POLYGON ((206568.581 449997.472, 206568.049 45...   
1810  POLYGON ((205479.878 447790.81, 205479.346 447...   
1811  POLYGON ((207183.164 447299.666, 207182.632 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
0      POINT (207522.39 449352.286)     0.0    1.0       0.0     0.0   
1     POINT (206809.893 451649.412)     0.0    0.0       0.0     0.0   
2     POINT (208413.146 451157.742)     0.0    0.0       0.0     0.0   
3     POINT (208925.569 448859.548)     0.0    0.0       0.0     0.0   
4     POINT (208216.265 450556.455)     0.0    0.0       0.0     0.0   
...                             ...     ...    ...       ...     ...   
1807  POINT (207826.225 448653.623)     0.0    0.0       0.0     0.0   
1808  POINT (208605.769 452559.326)     0.0    0.0       0.0     0.0   
1809  POINT (206618.333 450047.757)     0.0    0.0       0.0     0.0   
1810   POINT (205529.63 447841.094)     0.0    0.0       0.0     0.0   
1811   POINT (207232.916 447349.95)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  공영주차장_수  노인복지시설_수          공시지가  유소년_인구수  노인_인구수  인근공원_수  \
0           0.0      0.0       0.0  4.801408e+06     15.0    47.0     0.0   
1           0.0      0.0       0.0  2.813924e+06     18.0    48.0     0.0   
2           0.0      0.0       0.0  1.109825e+06     30.0   101.0     0.0   
3           0.0      0.0       0.0  2.578754e+06     71.0    26.0     0.0   
4           0.0      0.0       0.0  3.854859e+06     23.0   116.0     0.0   
...         ...      ...       ...           ...      ...     ...     ...   
1807        0.0      0.0       0.0  5.825167e+06      0.0     0.0     0.0   
1808        0.0      0.0       0.0  0.000000e+00      0.0     0.0     0.0   
1809        0.0      0.0       0.0  3.047138e+06      0.0     0.0     0.0   
1810        0.0      0.0       0.0  4.465999e+05      0.0     0.0     0.0   
1811        0.0      0.0       0.0  4.465999e+05      0.0     0.0     0.0   

      평균_기울기  
0      21.55  
1      15.32  
2      54.27  
3      15.17  
4      43.25  
...      ...  
1807   22.68  
1808  291.81  
1809   17.24  
1810    6.55  
1811    2.91  

[1812 rows x 17 columns]

# 데이터 정규화

---
 - 이진 결정트리나 랜덤 포레스트를 사용할 경우에는 정규화가 꼭 필요하진 않음
 - 결정트리는 각 변수의 값의 절대적인 크기가 아니라, 값의 분할 기준(threshold)을 기준으로 분기하기 때문에 스케일 차이의 영향을 크게 받지 않음
 ---
 - 머신러닝, 특히 결정트리 기반 이외의 모델(예: KNN, 선형회귀, 로지스틱 회귀, SVM 등)을 사용할 경우 **스케일이 큰 변수(예: 공시지가, 접근거리)**가 모델 학습에 영향을 크게 미쳐 정규화가 필요할 수 있음
   - 거리 기반 모델: KNN, K-Means, DBSCAN 등 사용 시에는 꼭 필요.
   - PCA, 시각화: 특성 간 비교 시 왜곡 방지를 위해 필요.
   - 지도 학습의 다른 모델: 결정트리가 아닌 모델을 쓰게 될 경우 (예: XGBoost, 선형모델) 대비해 미리 정규화해두는 것도 전략적일 수 있음
---

# 최종 예측용 데이터

In [ ]:
grid_gdf_child_parks

gid    lbl   val  \
0     다사633494  15.00  15.0   
1     다사626517  18.00  18.0   
2     다사642512  30.00  30.0   
3     다사647489  71.00  71.0   
4     다사640506  23.00  23.0   
...        ...    ...   ...   
1807  다사636487   None   NaN   
1808  다사644526   None   NaN   
1809  다사624501   None   NaN   
1810  다사613479   None   NaN   
1811  다사630474   None   NaN   

                                               geometry  \
0     POLYGON ((207472.637 449302.001, 207472.105 44...   
1     POLYGON ((206760.14 451599.127, 206759.608 451...   
2     POLYGON ((208363.394 451107.457, 208362.861 45...   
3     POLYGON ((208875.816 448809.263, 208875.284 44...   
4     POLYGON ((208166.512 450506.17, 208165.98 4506...   
...                                                 ...   
1807  POLYGON ((207776.472 448603.338, 207775.94 448...   
1808  POLYGON ((208556.016 452509.041, 208555.484 45...   
1809  POLYGON ((206568.581 449997.472, 206568.049 45...   
1810  POLYGON ((205479.878 447790.81, 205479.346 447...   
1811  POLYGON ((207183.164 447299.666, 207182.632 44...   

                           centroid  초등학교_수  유치원_수  지역아동센터_수  키즈카페_수  \
0      POINT (207522.39 449352.286)     0.0    1.0       0.0     0.0   
1     POINT (206809.893 451649.412)     0.0    0.0       0.0     0.0   
2     POINT (208413.146 451157.742)     0.0    0.0       0.0     0.0   
3     POINT (208925.569 448859.548)     0.0    0.0       0.0     0.0   
4     POINT (208216.265 450556.455)     0.0    0.0       0.0     0.0   
...                             ...     ...    ...       ...     ...   
1807  POINT (207826.225 448653.623)     0.0    0.0       0.0     0.0   
1808  POINT (208605.769 452559.326)     0.0    0.0       0.0     0.0   
1809  POINT (206618.333 450047.757)     0.0    0.0       0.0     0.0   
1810   POINT (205529.63 447841.094)     0.0    0.0       0.0     0.0   
1811   POINT (207232.916 447349.95)     0.0    0.0       0.0     0.0   

      청소년유해업소_수  공영주차장_수  노인복지시설_수          공시지가  유소년_인구수  노인_인구수  인근공원_수  \
0           0.0      0.0       0.0  4.801408e+06     15.0    47.0     0.0   
1           0.0      0.0       0.0  2.813924e+06     18.0    48.0     0.0   
2           0.0      0.0       0.0  1.109825e+06     30.0   101.0     0.0   
3           0.0      0.0       0.0  2.578754e+06     71.0    26.0     0.0   
4           0.0      0.0       0.0  3.854859e+06     23.0   116.0     0.0   
...         ...      ...       ...           ...      ...     ...     ...   
1807        0.0      0.0       0.0  5.825167e+06      0.0     0.0     0.0   
1808        0.0      0.0       0.0  0.000000e+00      0.0     0.0     0.0   
1809        0.0      0.0       0.0  3.047138e+06      0.0     0.0     0.0   
1810        0.0      0.0       0.0  4.465999e+05      0.0     0.0     0.0   
1811        0.0      0.0       0.0  4.465999e+05      0.0     0.0     0.0   

      평균_기울기  
0      21.55  
1      15.32  
2      54.27  
3      15.17  
4      43.25  
...      ...  
1807   22.68  
1808  291.81  
1809   17.24  
1810    6.55  
1811    2.91  

[1812 rows x 17 columns]

In [ ]:
grid_gdf_child_parks.isnull().sum()

gid            0
lbl          910
val          910
geometry       0
centroid       0
초등학교_수         0
유치원_수          0
지역아동센터_수       0
키즈카페_수         0
청소년유해업소_수      0
공영주차장_수        0
노인복지시설_수       0
공시지가           0
유소년_인구수        0
노인_인구수         0
인근공원_수         0
평균_기울기         0
dtype: int64

In [ ]:
grid_gdf_child_parks.dtypes

gid            object
lbl            object
val           float64
geometry     geometry
centroid     geometry
초등학교_수        float64
유치원_수         float64
지역아동센터_수      float64
키즈카페_수        float64
청소년유해업소_수     float64
공영주차장_수       float64
노인복지시설_수      float64
공시지가          float64
유소년_인구수       float64
노인_인구수        float64
인근공원_수        float64
평균_기울기        float64
dtype: object

In [ ]:
# grid_gdf_child_parks.to_csv('/content/drive/MyDrive/광진구 공모전 DB/광진구 공모전 데이터/최종_예측용_데이터(ver.2).csv', index=False)
# grid_gdf_child_parks.to_csv('/content/drive/MyDrive/광진구 공모전 DB/최종_예측용_데이터(ver.2).csv', index=False)